# Imports

In [2]:
import numpy as np
import pandas as pd
import plotly.express as px

from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split

from xgboost import XGBRegressor


pd.set_option('display.float_format', '{:.2f}'.format)

df = pd.read_csv("https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing.csv")

# Data Exploration

## Evaluating Outliers

In [ ]:
df

id             date  bedrooms  bathrooms  sqft_living  \
0      1565930130  20141104T000000         4       3.25         3760   
1      3279000420  20150115T000000         3       1.75         1460   
2       194000575  20141014T000000         4       1.00         1340   
3      2115510160  20141208T000000         3       1.75         1440   
4      7522500005  20140815T000000         2       1.50         1780   
...           ...              ...       ...        ...          ...   
19995  5272200045  20141113T000000         3       1.50         1000   
19996  9578500790  20141111T000000         3       2.50         3087   
19997  7202350480  20140930T000000         3       2.50         2120   
19998  1723049033  20140620T000000         1       0.75          380   
19999  6147650280  20150325T000000         4       2.50         3130   

       sqft_lot  floors  waterfront  view  condition  ...  sqft_basement  \
0          4675    2.00           0     0          3  ...           1020   
1          7800    1.00           0     0          2  ...            420   
2          5800    1.50           0     2          3  ...              0   
3          8050    1.00           0     0          3  ...              0   
4          4750    1.00           0     0          4  ...            700   
...         ...     ...         ...   ...        ...  ...            ...   
19995      6914    1.00           0     0          3  ...              0   
19996      5002    2.00           0     0          3  ...              0   
19997      4780    2.00           0     0          3  ...              0   
19998     15000    1.00           0     0          3  ...              0   
19999      5999    2.00           0     0          3  ...              0   

       yr_built  yr_renovated  zipcode   lat    long  sqft_living15  \
0          2007             0    98038 47.39 -122.05           3280   
1          1979             0    98023 47.30 -122.38           1310   
2          1914             0    98116 47.57 -122.39           1900   
3          1985             0    98023 47.32 -122.39           1790   
4          1947             0    98117 47.69 -122.39           1690   
...         ...           ...      ...   ...     ...            ...   
19995      1947             0    98125 47.71 -122.32           1000   
19996      2014             0    98023 47.30 -122.35           2927   
19997      2004             0    98053 47.68 -122.03           1690   
19998      1963             0    98168 47.48 -122.32           1170   
19999      2006             0    98042 47.38 -122.10           3020   

       sqft_lot15     price  yr_sold  
0            4033 429900.00     2014  
1            7865 233000.00     2015  
2            5800 455000.00     2014  
3            7488 258950.00     2014  
4            5962 555000.00     2014  
...           ...       ...      ...  
19995        6947 378000.00     2014  
19996        5183 399950.00     2014  
19997        2650 575000.00     2014  
19998       15000 245000.00     2014  
19999        5997 315000.00     2015  

[20000 rows x 22 columns]

In [ ]:
# Graphing out the distribution of various house sizes
sqft_count = (df["sqft_living"].floordiv(100)*100).value_counts().reset_index().sort_values("sqft_living")

fig1 = px.line(
    sqft_count,
    x="sqft_living",
    y="count"
)
fig1.show()

In [ ]:
# Graphing out the distribution of various house sizes
lot_count = (df["sqft_lot"].floordiv(100)*100).value_counts().reset_index().sort_values("sqft_lot")

fig2 = px.line(
    lot_count,
    x="sqft_lot",
    y="count"
)
fig2.show()

In [ ]:
# Graphing it again but excluding 
excluding_amount = 45000

lot_count = (df[df["sqft_lot"]<excluding_amount]["sqft_lot"].floordiv(500)*500).value_counts().reset_index().sort_values("sqft_lot")

fig2 = px.line(
    lot_count,
    x="sqft_lot",
    y="count"
)
fig2.show()

display(df[df["sqft_lot"]>excluding_amount])

id             date  bedrooms  bathrooms  sqft_living  \
56     2195700050  20140519T000000         4       2.50         3480   
63     2423069164  20150410T000000         3       2.00         1990   
77      522069119  20150512T000000         3       2.50         2720   
79      826069184  20141002T000000         3       2.50         1960   
92      824069173  20140821T000000         3       2.50         2320   
...           ...              ...       ...        ...          ...   
19872  1523069151  20140711T000000         2       1.00         1470   
19878  1823099056  20141222T000000         3       2.50         2810   
19936  9510320150  20141202T000000         4       2.50         2500   
19958  1522039105  20150115T000000         3       4.25         3300   
19960  3585300445  20140822T000000         3       1.75         2120   

       sqft_lot  floors  waterfront  view  condition  ...  sqft_above  \
56        59242    2.00           0     0          3  ...        3480   
63        65340    2.00           0     0          3  ...        1990   
77        62310    1.00           0     0          3  ...        2040   
79        47044    2.00           0     0          4  ...        1960   
92        52272    1.50           0     0          3  ...        2320   
...         ...     ...         ...   ...        ...  ...         ...   
19872     81021    1.00           0     0          4  ...        1470   
19878    435600    2.00           0     0          3  ...        2810   
19936     50595    2.00           0     0          3  ...        2500   
19958    308080    2.00           0     2          4  ...        2520   
19960     56192    1.00           0     1          3  ...        1720   

       sqft_basement  yr_built  yr_renovated  zipcode   lat    long  \
56                 0      1988             0    98072 47.74 -122.10   
63                 0      1986             0    98027 47.47 -121.99   
77               680      1985             0    98038 47.42 -122.07   
79                 0      1978             0    98077 47.76 -122.07   
92                 0      1974             0    98075 47.59 -122.07   
...              ...       ...           ...      ...   ...     ...   
19872              0      1949             0    98027 47.48 -122.03   
19878              0      1995             0    98045 47.48 -121.70   
19936              0      1997             0    98045 47.47 -121.73   
19958            780      1976             0    98070 47.40 -122.42   
19960            400      1959             0    98177 47.77 -122.37   

       sqft_living15  sqft_lot15     price  
56              2930       39400 810000.00  
63              2120       59241 500000.00  
77              2770      204296 550000.00  
79              2020       29004 535000.00  
92              2200       52272 600000.00  
...              ...         ...       ...  
19872           2600       69696 380000.00  
19878           2380       92007 745000.00  
19936           2765       33720 545000.00  
19958           2130       90604 729000.00  
19960           2240       20500 892500.00  

[934 rows x 21 columns]

In [ ]:
price_count = (df["price"].floordiv(10000)*10000).value_counts().reset_index().sort_values("price")

fig2 = px.line(
    price_count,
    x="price",
    y="count"
)
fig2.show()

In [ ]:
df[df["price"]>1500000]

id             date  bedrooms  bathrooms  sqft_living  \
13      251500330  20141014T000000         3       2.25         4320   
88     1224059053  20141027T000000         5       2.00         2500   
96     1068000255  20140827T000000         4       3.50         4285   
203    9412400220  20140710T000000         4       2.75         5470   
231    9315600050  20150317T000000         5       3.25         4560   
...           ...              ...       ...        ...          ...   
19886  3893100462  20150225T000000         5       3.75         4360   
19895  4139910160  20150401T000000         5       3.25         4320   
19916  3885803044  20140902T000000         4       5.00         5810   
19938  9362000040  20140623T000000         3       4.50         5230   
19994  5078400160  20140605T000000         5       4.50         4400   

       sqft_lot  floors  waterfront  view  condition  ...  sqft_above  \
13        19225    1.00           0     0          4  ...        2160   
88        15250    2.00           1     4          5  ...        2500   
96         9567    2.00           0     1          5  ...        3485   
203       18200    2.00           1     4          3  ...        3730   
231       19080    1.00           0     0          5  ...        2490   
...         ...     ...         ...   ...        ...  ...         ...   
19886      8504    2.00           0     4          3  ...        3530   
19895     32840    2.00           0     0          3  ...        4320   
19916      7440    2.00           0     0          3  ...        3790   
19938     17826    2.00           1     4          3  ...        3740   
19994     15580    2.00           0     0          3  ...        3390   

       sqft_basement  yr_built  yr_renovated  zipcode   lat    long  \
13              2160      1972             0    98004 47.64 -122.22   
88                 0      1942             0    98008 47.59 -122.11   
96               800      1946             0    98199 47.64 -122.41   
203             1740      1992             0    98118 47.53 -122.26   
231             2070      1963             0    98004 47.63 -122.23   
...              ...       ...           ...      ...   ...     ...   
19886            830      2014             0    98033 47.69 -122.19   
19895              0      1990             0    98006 47.55 -122.12   
19916           2020      2004             0    98033 47.69 -122.21   
19938           1490      2005             0    98040 47.53 -122.24   
19994           1010      2003             0    98004 47.62 -122.21   

       sqft_living15  sqft_lot15      price  
13              3430       18469 1775000.00  
88              1880       18782 1700000.00  
96              2960        6902 1650000.00  
203             3620       15100 1612500.00  
231             3390       20140 1675000.00  
...              ...         ...        ...  
19886           2680        9000 1789950.00  
19895           4410       33210 1600000.00  
19916           3010        7200 1875000.00  
19938           3670       17826 3400000.00  
19994           2150       14249 1800000.00  

[477 rows x 21 columns]

In [ ]:
yr = df["yr_built"].value_counts().reset_index().sort_values("yr_built")

fig5 = px.bar(
    yr,
    x="yr_built",
    y="count"
)
fig5.show()

In [ ]:
df["yr_sold"] = df["date"].str[0:4].to_numpy(np.int64)
df["yr_sold"].value_counts()

yr_sold
2014    13574
2015     6426
Name: count, dtype: int64

In [ ]:
duplicates = df[df["id"].duplicated(keep=False)].sort_values("id")

In [ ]:
duplicates

id             date  bedrooms  bathrooms  sqft_living  \
10022     1000102  20140916T000000         6       3.00         2400   
1272      1000102  20150422T000000         6       3.00         2400   
2124      7200179  20150424T000000         2       1.00          840   
11317     7200179  20141016T000000         2       1.00          840   
2103    109200390  20140820T000000         3       1.75         1480   
...           ...              ...       ...        ...          ...   
15385  9809000020  20140513T000000         5       2.25         3120   
13013  9834200305  20140716T000000         3       1.00         1790   
17200  9834200305  20150210T000000         3       1.00         1790   
3817   9834200885  20140717T000000         4       2.50         2080   
2130   9834200885  20150420T000000         4       2.50         2080   

       sqft_lot  floors  waterfront  view  condition  ...  sqft_basement  \
10022      9373    2.00           0     0          3  ...              0   
1272       9373    2.00           0     0          3  ...              0   
2124      12750    1.00           0     0          3  ...              0   
11317     12750    1.00           0     0          3  ...              0   
2103       3900    1.00           0     0          4  ...              0   
...         ...     ...         ...   ...        ...  ...            ...   
15385     16672    2.00           0     0          4  ...              0   
13013      3876    1.50           0     0          5  ...            700   
17200      3876    1.50           0     0          5  ...            700   
3817       4080    1.00           0     0          5  ...           1040   
2130       4080    1.00           0     0          5  ...           1040   

       yr_built  yr_renovated  zipcode   lat    long  sqft_living15  \
10022      1991             0    98002 47.33 -122.21           2060   
1272       1991             0    98002 47.33 -122.21           2060   
2124       1925             0    98055 47.48 -122.21           1480   
11317      1925             0    98055 47.48 -122.21           1480   
2103       1980             0    98023 47.30 -122.37           1830   
...         ...           ...      ...   ...     ...            ...   
15385      1969             0    98004 47.65 -122.22           3740   
13013      1904             0    98144 47.58 -122.29           1360   
17200      1904             0    98144 47.58 -122.29           1360   
3817       1962             0    98144 47.57 -122.29           1340   
2130       1962             0    98144 47.57 -122.29           1340   

       sqft_lot15      price  yr_sold  
10022        7316  280000.00     2014  
1272         7316  300000.00     2015  
2124         6969  175000.00     2015  
11317        6969  150000.00     2014  
2103         6956  245000.00     2014  
...           ...        ...      ...  
15385       17853 1895000.00     2014  
13013        4080  350000.00     2014  
17200        4080  615000.00     2015  
3817         4080  360000.00     2014  
2130         4080  550000.00     2015  

[308 rows x 22 columns]

# testing models

id             date  bedrooms  bathrooms  sqft_living  \
0      1565930130  20141104T000000         4       3.25         3760   
1      3279000420  20150115T000000         3       1.75         1460   
2       194000575  20141014T000000         4       1.00         1340   
3      2115510160  20141208T000000         3       1.75         1440   
4      7522500005  20140815T000000         2       1.50         1780   
...           ...              ...       ...        ...          ...   
19995  5272200045  20141113T000000         3       1.50         1000   
19996  9578500790  20141111T000000         3       2.50         3087   
19997  7202350480  20140930T000000         3       2.50         2120   
19998  1723049033  20140620T000000         1       0.75          380   
19999  6147650280  20150325T000000         4       2.50         3130   

       sqft_lot  floors  waterfront  view  condition  ...  yr_built  \
0          4675    2.00           0     0          3  ...      2007   
1          7800    1.00           0     0          2  ...      1979   
2          5800    1.50           0     2          3  ...      1914   
3          8050    1.00           0     0          3  ...      1985   
4          4750    1.00           0     0          4  ...      1947   
...         ...     ...         ...   ...        ...  ...       ...   
19995      6914    1.00           0     0          3  ...      1947   
19996      5002    2.00           0     0          3  ...      2014   
19997      4780    2.00           0     0          3  ...      2004   
19998     15000    1.00           0     0          3  ...      1963   
19999      5999    2.00           0     0          3  ...      2006   

       yr_renovated  zipcode   lat    long  sqft_living15  sqft_lot15  \
0                 0    98038 47.39 -122.05           3280        4033   
1                 0    98023 47.30 -122.38           1310        7865   
2                 0    98116 47.57 -122.39           1900        5800   
3                 0    98023 47.32 -122.39           1790        7488   
4                 0    98117 47.69 -122.39           1690        5962   
...             ...      ...   ...     ...            ...         ...   
19995             0    98125 47.71 -122.32           1000        6947   
19996             0    98023 47.30 -122.35           2927        5183   
19997             0    98053 47.68 -122.03           1690        2650   
19998             0    98168 47.48 -122.32           1170       15000   
19999             0    98042 47.38 -122.10           3020        5997   

          price  yr_sold  mnth_sold  
0     429900.00     2014         11  
1     233000.00     2015          1  
2     455000.00     2014         10  
3     258950.00     2014         12  
4     555000.00     2014          8  
...         ...      ...        ...  
19995 378000.00     2014         11  
19996 399950.00     2014         11  
19997 575000.00     2014          9  
19998 245000.00     2014          6  
19999 315000.00     2015          3  

[20000 rows x 23 columns]

In [15]:
df = df[df["price"]< 2000000]


# Base, no cleaning of data or parameter testing.
X = pd.get_dummies(df.drop(["price", "date"], axis=1))
X["yr_sold"] = df["date"].str[0:4].to_numpy(np.int64)
X["mnth_sold"] = df["date"].str[4:6].to_numpy(np.int64)
y = df["price"]

model = XGBRegressor()

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.2, random_state=42)

model.fit(X_train, y_train)

y_pred = model.predict(X_test)

sse = np.sum((y_test - y_pred) ** 2)
mse = mean_squared_error(y_test, y_pred)
rmse = np.sqrt(mse)
r2 = r2_score(y_test, y_pred)

display(sse)
display(mse)
display(rmse)
display(r2)



37710962537109.78

9515761427.481651

97548.76435650865

0.8807028756629424

In [3]:
mini = pd.read_csv("https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing_holdout_test_mini.csv")

X = pd.get_dummies(mini.drop(["date"], axis=1))
X["yr_sold"] = mini["date"].str[0:4].to_numpy(np.int64)
X["mnth_sold"] = mini["date"].str[4:6].to_numpy(np.int64)

X

id  bedrooms  bathrooms  sqft_living  sqft_lot  floors  \
0    930000305         4       1.75         2120      7680    1.00   
1   9541600015         4       2.25         2010     15375    1.00   
2   7338000150         2       1.00         1070      4200    1.00   
3   6113400046         4       2.50         1890     15770    2.00   
4    291310170         3       2.50         1600      2610    2.00   
..         ...       ...        ...          ...       ...     ...   
76  8902000267         4       2.75         2260      7209    1.00   
77  7856550240         5       2.25         3480      9200    2.00   
78  7923500060         5       2.75         2580      9242    2.00   
79  8898700880         2       2.00         1590      8000    1.00   
80  8123500050         5       2.75         2730     22572    1.00   

    waterfront  view  condition  grade  ...  sqft_basement  yr_built  \
0            0     0          4      7  ...           1060      1950   
1            0     0          4      8  ...              0      1957   
2            0     0          4      6  ...              0      1983   
3            0     0          4      7  ...              0      1968   
4            0     0          3      8  ...              0      2005   
..         ...   ...        ...    ...  ...            ...       ...   
76           0     3          3      7  ...            930      2002   
77           0     0          3      8  ...              0      1979   
78           0     2          4      8  ...            860      1967   
79           0     0          3      7  ...            680      1984   
80           0     0          3      7  ...            650      1968   

    yr_renovated  zipcode   lat    long  sqft_living15  sqft_lot15  yr_sold  \
0              0    98177 47.72 -122.36           1530        7680     2014   
1              0    98005 47.60 -122.17           1930       15375     2015   
2              0    98002 47.33 -122.22           1150        4200     2015   
3              0    98166 47.43 -122.34           2410       15256     2014   
4              0    98027 47.53 -122.07           1445        1288     2014   
..           ...      ...   ...     ...            ...         ...      ...   
76             0    98125 47.71 -122.30           1790       10860     2015   
77             0    98006 47.56 -122.15           3130        9200     2014   
78             0    98007 47.59 -122.13           2240        9316     2014   
79             0    98055 47.46 -122.20           1590        8364     2015   
80          1992    98075 47.60 -122.04           2260       15458     2014   

    mnth_sold  
0          11  
1           2  
2           1  
3           7  
4           8  
..        ...  
76          4  
77          7  
78          9  
79          3  
80          6  

[81 rows x 21 columns]

In [17]:

mini_pred = model.predict(X)
mini_pred = pd.DataFrame(mini_pred, columns = ['price'])
mini_pred.to_csv("Joseph-predictions.csv", index=False)




# Final Test

In [8]:
import numpy as np
import pandas as pd
import plotly.express as px

from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split

from xgboost import XGBRegressor


pd.set_option('display.float_format', '{:.2f}'.format)

df = pd.read_csv("https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing.csv")

df = df[df["price"]<4000000]





# df = df[df["price"]< 2000000]

# Base, no cleaning of data or parameter testing.
X = pd.get_dummies(df.drop(["price", "date"], axis=1))
X["yr_sold"] = df["date"].str[0:4].to_numpy(np.int64)
X["mnth_sold"] = df["date"].str[4:6].to_numpy(np.int64)
y = df["price"]

model = XGBRegressor()

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.2, random_state=42)

model.fit(X_train, y_train)



mini = pd.read_csv("https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing_holdout_test_mini.csv")

X = pd.get_dummies(mini.drop(["date"], axis=1))
X["yr_sold"] = mini["date"].str[0:4].to_numpy(np.int64)
X["mnth_sold"] = mini["date"].str[4:6].to_numpy(np.int64)


mini_pred = model.predict(X)
mini_pred = pd.DataFrame(mini_pred, columns = ['price'])
mini_pred.to_csv("Joseph-predictions.csv", index=False)


In [ ]:
targets_file = "https://raw.githubusercontent.com/byui-cse/cse450-course/master/data/housing_holdout_test_mini_answers.csv"
targets = pd.read_csv(targets_file)

In [20]:
mini.tail(20)

id             date  bedrooms  bathrooms  sqft_living  sqft_lot  \
61  4222310010  20150420T000000         4       1.00         1730      7350   
62  1226059161  20141229T000000         4       2.75         2560     83200   
63  1245003740  20140723T000000         3       2.00         1840      6000   
64  5553300375  20140820T000000         3       3.50         3080      6495   
65  3303000130  20150116T000000         3       2.25         1770      7667   
66  7606200090  20150327T000000         2       1.00         1160      5750   
67  8078700020  20140603T000000         3       2.25         1800     43647   
68  1974300020  20150218T000000         4       2.50         2270     11500   
69  2581300055  20141121T000000         3       3.25         2640     16090   
70   859000022  20140819T000000         3       2.50         1740      1844   
71  3013300409  20150312T000000         2       1.00         1220      6300   
72  2076400050  20141022T000000         4       2.25         1740      9600   
73  3530210260  20141027T000000         3       2.50         3030     45004   
74  7504100920  20140618T000000         3       3.00         3450     16200   
75  9528104660  20140827T000000         4       3.50         2980      3000   
76  8902000267  20150402T000000         4       2.75         2260      7209   
77  7856550240  20140710T000000         5       2.25         3480      9200   
78  7923500060  20140922T000000         5       2.75         2580      9242   
79  8898700880  20150317T000000         2       2.00         1590      8000   
80  8123500050  20140624T000000         5       2.75         2730     22572   

    floors  waterfront  view  condition  grade  sqft_above  sqft_basement  \
61    1.50           0     0          4      6        1730              0   
62    1.00           0     0          3      8        1860            700   
63    2.00           0     0          5      7        1720            120   
64    2.00           0     3          3     11        2530            550   
65    1.00           0     0          3      8        1270            500   
66    1.00           0     0          4      6        1160              0   
67    1.00           0     0          4      8        1800              0   
68    1.00           0     0          3      8        1540            730   
69    1.00           0     2          4      8        1960            680   
70    2.00           0     0          3      8        1320            420   
71    1.00           0     0          3      7         760            460   
72    1.00           0     2          3      7        1160            580   
73    2.00           0     0          3      9        3030              0   
74    2.00           0     0          3     10        3450              0   
75    2.00           0     0          3      9        2340            640   
76    1.00           0     3          3      7        1330            930   
77    2.00           0     0          3      8        3480              0   
78    2.00           0     2          4      8        1720            860   
79    1.00           0     0          3      7         910            680   
80    1.00           0     0          3      7        2080            650   

    yr_built  yr_renovated  zipcode   lat    long  sqft_living15  sqft_lot15  
61      1970             0    98003 47.35 -122.31           1440        7752  
62      1980             0    98072 47.75 -122.11           1990       38332  
63      1946             0    98033 47.68 -122.21           1390        6000  
64      1996          2006    98199 47.63 -122.39           4120        8620  
65      1966             0    98177 47.77 -122.36           2180        8103  
66      1924             0    98065 47.53 -121.83           1160        8250  
67      1976             0    98072 47.78 -122.13           2480       25608  
68      1967             0    98034 47.71 -122.24           2020       10918  
69      1976           

In [7]:
df = df[df["price"]<4000000]

figx = px.scatter(
    df,
    x="long",
    y="lat",
    color="price",
    color_continuous_scale=[(0, "red"), (.2, "green")],
    hover_data="zipcode"
    
)
figx.show()

# Update layout to make x and y axes scale evenly
figx.update_layout(
    yaxis=dict(scaleanchor="x", scaleratio=1),  # Ensure equal scaling between x and y
    xaxis=dict(scaleanchor="y", scaleratio=1)
)

# Display the figure
figx.show()

In [30]:
df

Empty DataFrame
Columns: [id, date, bedrooms, bathrooms, sqft_living, sqft_lot, floors, waterfront, view, condition, grade, sqft_above, sqft_basement, yr_built, yr_renovated, zipcode, lat, long, sqft_living15, sqft_lot15, price]
Index: []

[0 rows x 21 columns]